<a href="https://colab.research.google.com/github/Aravinnthram/CDW-Intern/blob/Day4/BERT2_0.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Embeddings**

In [ ]:
from transformers import AutoModel, AutoTokenizer

# Load a tokenizer
tokenizer = AutoTokenizer.from_pretrained('bert-base-uncased')

# Load a language model
model = AutoModel.from_pretrained('bert-base-uncased')

##microsoft/deberta-v3-xsmall

# Tokenize the sentence
tokens = tokenizer('Hello world', return_tensors='pt')

# Process the tokens
output = model(**tokens)[0]

In [ ]:
output.shape

torch.Size([1, 4, 768])

In [ ]:
for token in tokens['input_ids'][0]:
    print(tokenizer.decode(token))

[CLS]
hello
world
[SEP]


In [ ]:
output

tensor([[[-0.1689,  0.1361, -0.1394,  ..., -0.6251,  0.0522,  0.3671],
         [-0.3633,  0.1412,  0.8800,  ...,  0.1043,  0.2888,  0.3727],
         [-0.6986, -0.6988,  0.0645,  ..., -0.2210,  0.0099, -0.5940],
         [ 0.8310,  0.1237, -0.1512,  ...,  0.1031, -0.6779, -0.2629]]],
       grad_fn=<NativeLayerNormBackward0>)

**Scaled Dot Product Attention**

In [ ]:
from transformers import BertModel

In [ ]:
model = BertModel.from_pretrained('bert-base-uncased')

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

In [ ]:
len(model.encoder.layer)

12

In [ ]:
model.encoder.layer[0]

BertLayer(
  (attention): BertAttention(
    (self): BertSdpaSelfAttention(
      (query): Linear(in_features=768, out_features=768, bias=True)
      (key): Linear(in_features=768, out_features=768, bias=True)
      (value): Linear(in_features=768, out_features=768, bias=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (output): BertSelfOutput(
      (dense): Linear(in_features=768, out_features=768, bias=True)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
  )
  (intermediate): BertIntermediate(
    (dense): Linear(in_features=768, out_features=3072, bias=True)
    (intermediate_act_fn): GELUActivation()
  )
  (output): BertOutput(
    (dense): Linear(in_features=3072, out_features=768, bias=True)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
)

In [ ]:
model.encoder.layer[0].attention

BertAttention(
  (self): BertSdpaSelfAttention(
    (query): Linear(in_features=768, out_features=768, bias=True)
    (key): Linear(in_features=768, out_features=768, bias=True)
    (value): Linear(in_features=768, out_features=768, bias=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (output): BertSelfOutput(
    (dense): Linear(in_features=768, out_features=768, bias=True)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
)

**Multi Headed Attention**

In [ ]:
from transformers import BertConfig
config = BertConfig()
config

BertConfig {
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "position_embedding_type": "absolute",
  "transformers_version": "4.47.1",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 30522
}

In [ ]:
!pip install bertviz

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.6/157.6 kB 4.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.2/139.2 kB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 27.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 5.1 MB/s eta 0:00:00


In [ ]:
from transformers import BertModel, BertTokenizer
from bertviz import head_view
import torch
import pandas as pd

In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased')

In [ ]:
text = "My friend told me about this series and I loved it so far! She was Right"

token = tokenizer.encode(text)

input = torch.tensor(token).unsqueeze(0)

input

tensor([[ 101, 2026, 2767, 2409, 2033, 2055, 2023, 2186, 1998, 1045, 3866, 2009,
         2061, 2521,  999, 2016, 2001, 2157,  102]])

In [ ]:
# Show full cell output
pd.set_option("display.max_colwidth", None)

df[df["label"] != df["predicted_label"]].head(2)

(tensor([[[[3.9918e-02, 4.1166e-02, 2.4618e-02,  ..., 3.2405e-02,
            7.9816e-02, 1.8992e-01],
           [4.7139e-02, 8.4563e-02, 4.0671e-02,  ..., 5.6479e-02,
            3.5938e-02, 6.9000e-02],
           [3.9980e-02, 7.0939e-02, 3.5259e-02,  ..., 3.8825e-02,
            3.2888e-02, 4.9496e-02],
           ...,
           [4.9451e-02, 4.8452e-02, 3.6984e-02,  ..., 1.0205e-01,
            2.0156e-02, 1.9931e-02],
           [3.7765e-02, 6.6840e-02, 4.1755e-02,  ..., 2.6256e-02,
            2.1105e-02, 5.2181e-02],
           [3.6807e-02, 5.9701e-02, 3.2397e-02,  ..., 4.1644e-02,
            4.1940e-02, 6.7538e-02]],
 
          [[6.6242e-01, 7.2827e-03, 5.2428e-03,  ..., 1.5649e-02,
            8.7362e-03, 6.1327e-03],
           [8.2279e-03, 1.0128e-02, 3.3624e-01,  ..., 4.7440e-03,
            7.0783e-02, 1.4988e-02],
           [5.3907e-03, 1.9672e-02, 8.6874e-02,  ..., 1.0809e-02,
            7.1106e-02, 3.7451e-02],
           ...,
           [2.1296e-03, 2.6486e-02, 8.

In [ ]:
#average attention in all heads
final_attention = attention[-1].mean(1)[0]
final_attention.size()

torch.Size([19, 19])

In [ ]:
import pandas as pd

In [ ]:
attention_df = pd.DataFrame(final_attention.detach()).applymap(float).round(3)

attention_df.columns = tokenizer.convert_ids_to_tokens(token)
attention_df.index = tokenizer.convert_ids_to_tokens(token)

attention_df

<ipython-input-33-0a22402279a2>:1: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  attention_df = pd.DataFrame(final_attention.detach()).applymap(float).round(3)


[CLS]     my  friend   told     me  about   this  series    and  \
[CLS]   0.075  0.035   0.019  0.010  0.008  0.020  0.048   0.103  0.031   
my      0.017  0.027   0.014  0.008  0.012  0.016  0.018   0.014  0.017   
friend  0.016  0.013   0.149  0.011  0.004  0.007  0.008   0.011  0.008   
told    0.009  0.005   0.012  0.094  0.003  0.012  0.006   0.007  0.005   
me      0.022  0.014   0.008  0.010  0.016  0.013  0.011   0.010  0.015   
about   0.017  0.010   0.006  0.023  0.008  0.077  0.018   0.018  0.013   
this    0.022  0.012   0.004  0.007  0.007  0.020  0.054   0.035  0.016   
series  0.023  0.010   0.005  0.006  0.005  0.012  0.031   0.067  0.012   
and     0.031  0.017   0.006  0.007  0.011  0.008  0.014   0.011  0.093   
i       0.019  0.013   0.007  0.008  0.012  0.012  0.012   0.012  0.017   
loved   0.013  0.006   0.006  0.020  0.005  0.010  0.009   0.007  0.007   
it      0.021  0.008   0.005  0.008  0.009  0.017  0.034   0.039  0.015   
so      0.021  0.015   0.008  0.013  0.017  0.020  0.023   0.022  0.017   
far     0.016  0.009   0.004  0.008  0.013  0.017  0.026   0.023  0.018   
!       0.028  0.014   0.004  0.004  0.005  0.006  0.012   0.009  0.030   
she     0.027  0.012   0.024  0.021  0.005  0.006  0.007   0.008  0.013   
was     0.031  0.013   0.014  0.015  0.006  0.007  0.009   0.011  0.014   
right   0.075  0.015   0.008  0.013  0.006  0.014  0.014   0.012  0.009   
[SEP]   0.015  0.005   0.002  0.002  0.002  0.002  0.005   0.008  0.006   

            i  loved     it     so    far      !    she    was  right  [SEP]  
[CLS]   0.019  0.021  0.037  0.008  0.030  0.056  0.059  0.083  0.138  0.202  
my      0.014  0.012  0.015  0.009  0.008  0.015  0.024  0.031  0.034  0.694  
friend  0.005  0.010  0.007  0.004  0.004  0.006  0.018  0.010  0.008  0.698  
told    0.003  0.014  0.006  0.005  0.003  0.005  0.006  0.005  0.008  0.794  
me      0.013  0.010  0.010  0.005  0.007  0.015  0.007  0.007  0.013  0.795  
about   0.005  0.016  0.019  0.007  0.008  0.009  0.006  0.005  0.011  0.723  
this    0.007  0.009  0.033  0.009  0.010  0.014  0.007  0.006  0.012  0.717  
series  0.006  0.007  0.021  0.007  0.009  0.015  0.006  0.005  0.008  0.746  
and     0.010  0.009  0.012  0.011  0.009  0.024  0.014  0.014  0.018  0.682  
i       0.022  0.011  0.012  0.006  0.009  0.019  0.015  0.011  0.019  0.763  
loved   0.006  0.105  0.008  0.007  0.012  0.010  0.008  0.010  0.014  0.738  
it      0.007  0.012  0.067  0.014  0.014  0.010  0.009  0.006  0.009  0.695  
so      0.013  0.016  0.029  0.037  0.022  0.018  0.013  0.018  0.023  0.656  
far     0.012  0.014  0.025  0.017  0.054  0.010  0.005  0.006  0.009  0.714  
!       0.009  0.015  0.007  0.008  0.008  0.057  0.008  0.011  0.020  0.745  
she     0.007  0.013  0.008  0.005  0.005  0.012  0.062  0.042  0.026  0.696  
was     0.008  0.014  0.011  0.009  0.008  0.015  0.055  0.103  0.049  0.606  
right   0.009  0.022  0.011  0.006  0.007  0.016  0.017  0.034  0.124  0.591  
[SEP]   0.003  0.004  0.003  0.003  0.004  0.008  0.004  0.004  0.006  0.912

In [ ]:
tokens_as_list = tokenizer.convert_ids_to_tokens(input[0])
head_view(attention, tokens_as_list)

#2 - Previous & 6 - Pronouns

<IPython.core.display.Javascript object>

In [ ]:
#previous tokens
head_view(attention,tokenizer.convert_ids_to_tokens(input[0]),layer=2, heads=[0])

<IPython.core.display.Javascript object>

In [ ]:
#object - verb
head_view(attention,tokenizer.convert_ids_to_tokens(input[0]),layer=7, heads=[9])

<IPython.core.display.Javascript object>

In [ ]:
eight_ten = attention[7][0][9]

In [ ]:
attention_df = pd.DataFrame(eight_ten.detach()).applymap(float).round(3)

attention_df.columns = tokenizer.convert_ids_to_tokens(token)
attention_df.index = tokenizer.convert_ids_to_tokens(token)

attention_df

#me -> told
#it -> love
#right -> she

<ipython-input-38-a04302c25f99>:1: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  attention_df = pd.DataFrame(eight_ten.detach()).applymap(float).round(3)


[CLS]     my  friend   told     me  about   this  series    and  \
[CLS]   0.010  0.005   0.010  0.003  0.002  0.002  0.006   0.006  0.003   
my      0.041  0.028   0.024  0.005  0.002  0.001  0.001   0.001  0.005   
friend  0.027  0.147   0.034  0.002  0.001  0.000  0.001   0.000  0.004   
told    0.055  0.076   0.021  0.013  0.004  0.002  0.001   0.000  0.001   
me      0.012  0.008   0.006  0.758  0.011  0.005  0.001   0.000  0.001   
about   0.018  0.016   0.028  0.282  0.019  0.010  0.007   0.001  0.003   
this    0.009  0.002   0.021  0.249  0.023  0.374  0.052   0.007  0.003   
series  0.025  0.001   0.004  0.095  0.012  0.149  0.154   0.038  0.005   
and     0.043  0.010   0.002  0.070  0.017  0.100  0.023   0.004  0.044   
i       0.029  0.025   0.009  0.233  0.010  0.022  0.004   0.001  0.311   
loved   0.014  0.003   0.001  0.004  0.001  0.001  0.001   0.001  0.151   
it      0.005  0.001   0.006  0.042  0.002  0.123  0.023   0.004  0.018   
so      0.006  0.003   0.001  0.002  0.000  0.000  0.001   0.000  0.037   
far     0.015  0.007   0.002  0.004  0.002  0.001  0.007   0.001  0.038   
!       0.007  0.005   0.001  0.002  0.001  0.000  0.001   0.001  0.022   
she     0.010  0.005   0.002  0.001  0.000  0.000  0.001   0.000  0.006   
was     0.023  0.006   0.002  0.004  0.001  0.001  0.000   0.000  0.002   
right   0.034  0.007   0.004  0.014  0.003  0.001  0.002   0.001  0.005   
[SEP]   0.017  0.007   0.004  0.003  0.003  0.003  0.007   0.004  0.007   

            i  loved     it     so    far      !    she    was  right  [SEP]  
[CLS]   0.002  0.003  0.006  0.003  0.007  0.008  0.012  0.023  0.040  0.849  
my      0.001  0.001  0.001  0.000  0.002  0.030  0.003  0.006  0.050  0.798  
friend  0.001  0.000  0.000  0.000  0.002  0.017  0.002  0.005  0.020  0.735  
told    0.000  0.000  0.000  0.000  0.001  0.010  0.001  0.001  0.018  0.795  
me      0.000  0.000  0.000  0.000  0.000  0.002  0.000  0.000  0.016  0.180  
about   0.000  0.000  0.000  0.000  0.001  0.003  0.002  0.001  0.044  0.564  
this    0.001  0.002  0.001  0.001  0.005  0.001  0.001  0.001  0.017  0.231  
series  0.001  0.008  0.009  0.002  0.009  0.006  0.008  0.003  0.097  0.374  
and     0.011  0.005  0.001  0.001  0.002  0.009  0.001  0.002  0.009  0.649  
i       0.026  0.013  0.000  0.002  0.002  0.009  0.000  0.000  0.004  0.299  
loved   0.193  0.060  0.003  0.002  0.002  0.003  0.000  0.000  0.002  0.557  
it      0.013  0.663  0.012  0.005  0.009  0.002  0.001  0.000  0.005  0.067  
so      0.024  0.028  0.005  0.004  0.011  0.006  0.001  0.000  0.002  0.868  
far     0.078  0.097  0.113  0.079  0.008  0.022  0.007  0.006  0.006  0.508  
!       0.017  0.006  0.007  0.009  0.009  0.027  0.006  0.002  0.004  0.873  
she     0.002  0.017  0.010  0.010  0.011  0.106  0.046  0.038  0.033  0.701  
was     0.000  0.007  0.001  0.002  0.006  0.132  0.153  0.092  0.168  0.399  
right   0.001  0.003  0.002  0.001  0.004  0.044  0.130  0.145  0.093  0.506  
[SEP]   0.005  0.004  0.005  0.002  0.007  0.015  0.008  0.005  0.016  0.879

The Masked Language Model

In [ ]:
from transformers import BertForMaskedLM, pipeline

In [ ]:
bert_lm = BertForMaskedLM.from_pretrained('bert-base-uncased')

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [ ]:
bert_lm

BertForMaskedLM(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwi

In [ ]:
nlp = pipeline("fill-mask", model="bert-base-cased")

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/436M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

Device set to use cpu


In [ ]:
type(nlp.model)

transformers.models.bert.modeling_bert.BertForMaskedLM

In [ ]:
nlp.tokenizer

BertTokenizerFast(name_or_path='bert-base-cased', vocab_size=28996, model_max_length=512, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=False, added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	100: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	101: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	102: AddedToken("[SEP]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	103: AddedToken("[MASK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}
)

In [ ]:
print(type(nlp.model))

preds = nlp(f"If you don't {nlp.tokenizer.mask_token} at the sign, you will get a ticket")

print("If you don't *** at the sign, you will get a ticket")

for p in preds:
  print(f"Token: {p['token_str']}, Score: {p['score']}")

<class 'transformers.models.bert.modeling_bert.BertForMaskedLM'>
If you don't *** at the sign, you will get a ticket
Token: look, Score: 0.4699697196483612
Token: stop, Score: 0.4314803183078766
Token: glance, Score: 0.008274484425783157
Token: wait, Score: 0.007631904911249876
Token: turn, Score: 0.006474772933870554


**Next Sentence Prediction**

In [ ]:
from transformers import BertForNextSentencePrediction, pipeline
import torch

In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_nsp = BertForNextSentencePrediction.from_pretrained('bert-base-uncased')

In [ ]:
text1 = "I am Batman"
text2 = "I save Gotham from criminals"

In [ ]:
inputs = tokenizer(text1, text2, return_tensors='pt')

inputs

{'input_ids': tensor([[  101,  1045,  2572,  8942,   102,  1045,  3828, 22814,  2013, 12290,
           102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}

In [ ]:
outputs = bert_nsp(**inputs)

outputs

NextSentencePredictorOutput(loss=None, logits=tensor([[ 5.8279, -5.4549]], grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

**Finetuning BERT**

In [ ]:
from transformers import BertForSequenceClassification, BertForQuestionAnswering, BertForTokenClassification

In [ ]:
bert_sq = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels = 3)
bert_sq

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e

In [ ]:
bert_sq.classifier

Linear(in_features=768, out_features=3, bias=True)

In [ ]:
finbert = pipeline('text-classification', model='ProsusAI/finbert', tokenizer='ProsusAI/finbert')

config.json:   0%|          | 0.00/758 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/438M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/252 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

Device set to use cpu


In [ ]:
finbert("Nifty ended high today")

[{'label': 'positive', 'score': 0.8366928696632385}]

In [ ]:
finbert.model

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e

**Token Classification**

In [ ]:
bert_tc = BertForTokenClassification.from_pretrained('bert-base-uncased')
bert_tc

Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


BertForTokenClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12

In [ ]:
bert_tc.classifier

Linear(in_features=768, out_features=2, bias=True)

In [ ]:
custom_model = 'savasy/bert-base-turkish-ner-cased'
ner = pipeline('ner', model=custom_model, tokenizer=custom_model)

config.json:   0%|          | 0.00/734 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/443M [00:00<?, ?B/s]

Some weights of the model checkpoint at savasy/bert-base-turkish-ner-cased were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


tokenizer_config.json:   0%|          | 0.00/40.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/251k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

Device set to use cpu


In [ ]:
sequence = "Benim adım Johan ve India'danım"
ner(sequence)

[{'entity': 'B-PER',
  'score': 0.56859535,
  'index': 3,
  'word': 'Johan',
  'start': 11,
  'end': 16},
 {'entity': 'B-ORG',
  'score': 0.44022468,
  'index': 5,
  'word': 'In',
  'start': 20,
  'end': 22},
 {'entity': 'I-ORG',
  'score': 0.7260703,
  'index': 6,
  'word': '##dia',
  'start': 22,
  'end': 25}]

**Question/Answering**

In [ ]:
bert_qa = BertForQuestionAnswering.from_pretrained('bert-base-uncased')
bert_qa

Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


BertForQuestionAnswering(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, 

In [ ]:
bert_qa.qa_outputs

Linear(in_features=768, out_features=2, bias=True)

In [ ]:
model_name = 'deepset/roberta-base-squad2'

qa = pipeline(task ='question-answering', model=model_name, tokenizer=model_name)

config.json:   0%|          | 0.00/571 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/496M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/79.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/772 [00:00<?, ?B/s]

Device set to use cpu


In [ ]:
input = "Who is Batman","Mukesh is Batman while Matt is Superman"
qa(*input)


/usr/local/lib/python3.11/dist-packages/transformers/pipelines/question_answering.py:391: FutureWarning: Passing a list of SQuAD examples to the pipeline is deprecated and will be removed in v5. Inputs should be passed using the `question` and `context` keyword arguments instead.
  warnings.warn(


{'score': 0.05430568754673004, 'start': 0, 'end': 6, 'answer': 'Mukesh'}

In [ ]:
input = "Who is Superman","Mukesh is Batman while Matt is Superman"
qa(*input)


{'score': 0.0055078137665987015, 'start': 23, 'end': 27, 'answer': 'Matt'}